
# Accelerating Data Science with Databricks AutoML

##  Predicting patient readmission risk: Single click deployment with AutoML

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/hls/patient-readmission/patient-risk-ds-flow-2.png?raw=true" width="700px" style="float: right; margin-left: 10px;" />


In this notebook, we will explore how to use Databricks AutoML to generate the best notebooks to predict our patient readmission risk and deploy our model in production.

Databricks AutoML allows you to quickly generate baseline models and notebooks. 

ML experts can accelerate their workflow by fast-forwarding through the usual trial-and-error and focus on customizations using their domain knowledge, and citizen data scientists can quickly achieve usable results with a low-code approach.

In [0]:
dbutils.widgets.text("catalog", "", "Catalog")
dbutils.widgets.text("schema", "", "Schema")

In [0]:
from pyspark.sql import SparkSession
spark: SparkSession

catalog = dbutils.widgets.get("catalog")
schema = dbutils.widgets.get("schema")

spark.sql(f"USE `{catalog}`.`{schema}`")

DataFrame[]

In [0]:
import mlflow
mlflow.set_registry_uri("databricks-uc")

### Getting our training dataset 

Let's use the our training dataset determinining the readmission after 30 days for all our population. We will use that as our training label and what we want our model to predict.

In [0]:
training_dataset = spark.sql(f"""
                      SELECT 
                      b.*
                      , a.claim_amount
                      FROM ddavis_hls_sql.ai.training_patient_claims a 
                      INNER JOIN ddavis_hls_sql.ai.feature_beneficiary b ON a.beneficiary_code = b.beneficiary_code
                      """)

training_dataset.write.mode("overwrite").saveAsTable("ddavis_hls_sql.ai.training_dataset")

display(training_dataset)

beneficiary_code date_of_birth date_of_death gender race esrd_flag state county_code heart_failure_flag cronic_kidney_disease_flag cancer_flag copd_flag depression_flag diabetes_flag ischemic_heart_disease_flag osteoporosis_flag asrheumatoid_arthritis_flag stroke_transient_ischemic_attack_flag claim_amount FF54A63FA55F5556 1954-03-01 null Male Black No WA 220 No No No No Yes No No No No No 13940.0 FF5FA9DFBDCB7632 1926-01-01 null Female White Yes MD 150 Yes Yes Yes Yes No Yes Yes No Yes No 47150.0 FFB3ECE3201A4722 1954-12-01 null Female Black No VA 921 No No No No No Yes No No No No 5020.0 FFF58E99961D73D2 1932-12-01 null Female White Yes CO 340 Yes No No No No No No No No No 1000.0 000DFFF54425C08E 1943-10-01 null Female White No IN 880 Yes No No Yes No No Yes No No No 28500.0 0019EF0547183BF0 1945-12-01 2010-02-01 Male White No LA 250 No Yes No No Yes Yes Yes No No No 90860.0 0023288365A51F33 1949-05-01 null Female White No MA 020 Yes No No No No No No No No No 38000.0 0027B2294564172E 1925-05-01 null Female White No AR 650 Yes No No No No Yes No No Yes No 21580.0 00398D4814D4CBD9 1935-07-01 null Male White No NJ 160 Yes No No Yes No No Yes No No No 9230.0 003D116838833B5A 1924-02-01 2010-05-01 Male Others No CA 200 No No No No No No No No No No 7520.0 004CE7E5EA809119 1950-09-01 null Female White No WV 540 No No No No No Yes Yes Yes No No 16000.0 005B5479DF30DA8F 1977-07-01 null Male White No PA 210 No No No No Yes Yes Yes No Yes No 5520.0 005BB60274E463F1 1928-01-01 null Male White No WI 660 Yes No No No No No No No No No 170.0 0069E64C57A15880 1939-05-01 null Female Others No NY 590 Yes Yes No No Yes Yes Yes No No No 5470.0 006EDA9FD8D21C5D 1941-02-01 null Male White No LA 160 No No No No No No Yes No No No 880.0 00A31960C9C84164 1914-09-01 null Female White No WI 140 Yes No No No Yes No Yes No Yes No 18410.0 00A3A4FFB3FF3F14 1923-11-01 null Female White No IN 880 No No No No No Yes Yes No No No 2680.0 00A50EE01B2F02C5 1937-03-01 null Female White No PA 560 No No No No No No Yes Yes Yes No 1500.0 00FA82286C92C447 1921-07-01 null Female White No CA 430 No No No No No Yes Yes No No No 3020.0 01081B06186F35BF 1941-10-01 null Male White Yes MN 260 No Yes No No Yes Yes Yes No No No 28410.0 01106D77AE26495F 1935-07-01 null Male White No TX 451 Yes No No No No Yes No Yes No No 60.0 01120EFF103F861F 1948-09-01 null Male White No CO 200 No No No No No No No No No No 50.0 0148A2944DF71C22 1933-06-01 null Female White No LA 250 No Yes No No No Yes Yes No No No 31500.0 0164E18CAA3B4BC4 1924-10-01 null Male White No FL 470 Yes No No No No Yes Yes No No No 1420.0 016EBEB67308D32C 1951-03-01 null Male Others No TX 610 Yes No No No No No No No No No 800.0 0195854951CCF8F6 1938-07-01 null Male White No FL 500 No Yes No No No No No No No No 32340.0 01B2318DF09DD10D 1940-02-01 null Male White No NY 240 No No No No Yes No No No No No 3030.0 01FBE917EFC1A50C 1942-08-01 null Male White No NV 010 No No No No No No No Yes No No 480.0 01FE23095E46DB40 1922-09-01 null Female White No TX 480 Yes No No Yes Yes No No Yes No No 10250.0 0202E8D0EE5948FA 1932-09-01 2009-02-01 Female White No WI 390 Yes Yes No No No Yes Yes Yes No No 3430.0 020C294F456F09E6 1932-09-01 2008-11-01 Male White No OH 580 No No No Yes No No Yes No No No 1550.0 0265CD7D74F416CF 1921-03-01 null Female White No TX 758 Yes No No No No Yes Yes Yes Yes No 5770.0 026B6442700FECBD 1919-07-01 null Female White No PA 320 No No No No Yes Yes Yes No No No 46320.0 026FCC30F330B983 1936-01-01 null Male White No FL 410 No No No No No No No No No No 680.0 027C73B2F6484BEB 1957-09-01 null Male White No OH 310 No No No No No No Yes No No No 44830.0 027DD1FAE481507E 1933-03-01 null Female White No KY 750 No No No No Yes No No No No No 310.0 0280069A72228C77 1941-11-01 null Male White No Others 030 No Yes No No No No Yes No No No 7640.0 028253A641B0903D 1936-04-01 null Male White No NY 520 No No No No No No No No No No 3490.0 028B1AEBCD7E0EBE 1935-05-01 null Male White No IL 570 Yes No No No No N

### Define what features to look up for our model

Let's only keep the relevant features for our model training. We are removing columns such as `SSN` or `IDs`.

This step could also be done selecting the training_dataset table from the UI and selecting the column of interest.

*Note: this could also be retrived from our Feature Store tables. For more details on that open the companion notebook.*

In [0]:
all_columns = training_dataset.columns
feature_names = ["race", "date_of_birth", "stroke_transient_ischemic_attack_flag", "cronic_kidney_disease_flag", "esrd_flag", "county_code", "diabetes_flag", "cancer_flag", "state", "copd_flag", "gender", "heart_failure_flag", "asrheumatoid_arthritis_flag", "depression_flag", "date_of_death", "ischemic_heart_disease_flag", "osteoporosis_flag"]

excluded_columns = [c for c in all_columns if c not in feature_names]

In [0]:
excluded_columns

['beneficiary_code', 'claim_amount']

In [0]:
from databricks import automl
summary = automl.regress(training_dataset, target_col="claim_amount", exclude_cols=excluded_columns, primary_metric="mae", timeout_minutes=30)

2024/11/27 22:05:57 INFO databricks.automl.client.manager: AutoML will optimize for mean absolute error metric, which is tracked as val_mean_absolute_error in the MLflow experiment.
2024/11/27 22:05:58 INFO databricks.automl.client.manager: MLflow Experiment ID: 3582014443838527
2024/11/27 22:05:58 INFO databricks.automl.client.manager: MLflow Experiment: https://e2-demo-field-eng.cloud.databricks.com/?o=1444828305810485#mlflow/experiments/3582014443838527
2024/11/27 22:07:01 INFO databricks.automl.client.manager: Data exploration notebook: https://e2-demo-field-eng.cloud.databricks.com/?o=1444828305810485#notebook/3582014443838552


## Deploying our model in production

Our model is now ready. We can review the notebook generated by the auto-ml run and customize if if required.

For this demo, we'll consider that our model is ready and deploy it in production in our Model Registry:

In [0]:
model_name = f"{catalog}.{schema}.claims_prediction_model"
model_registered = mlflow.register_model(f"runs:/{summary.best_trial.mlflow_run_id}/model", model_name)

#Move the model in production
client = mlflow.tracking.MlflowClient()
print("registering model version "+model_registered.version+" as production model")
client.set_registered_model_alias(model_name, "Production", model_registered.version)

com.databricks.backend.common.rpc.CommandCancelledException
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:445)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperation$1(UsageLogging.scala:527)
	at com.databricks.logging.UsageLogging.executeThunkAndCaptureResultTags$1(UsageLogging.scala:631)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperationWithResultTags$4(UsageLogging.scala:651)
	at com.databricks.logging.AttributionContextTracing.$anonfun$withAttributionContext$1(AttributionContextTracing.scala:48)
	at com.databricks.logging.AttributionContext$.$anonfun$withValue$1(AttributionContext.scala:276)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:62)
	at com.databricks.logging.AttributionContext$.withValue(Attr

We just moved our automl model as production ready! 

Open [the dbdemos_hls_patient_readmission model](#mlflow/models/dbdemos_hls_patient_readmission) to explore its artifact and analyze the parameters used, including traceability to the notebook used for its creation.


## Our model predicting default risks is now deployed in production

So far we have:
* ingested all required data in a single source of truth using the OMOP data model,
* properly secured all data (including granting granular access controls, masked PII data, applied column level filtering),
* enhanced that data through feature engineering (and Feature Store as an option),
* used MLFlow AutoML to track experiments and build a machine learning model,
* registered the model.

### Next steps
We're now ready to use our model use it for:

- Batch inferences in notebook [04.3-Batch-Scoring-patient-readmission]($./04.3-Batch-Scoring-patient-readmission) to start using it for identifying patient at risk and providing cusom care to reduce readmission risk,
- Real time inference with [04.4-Model-Serving-patient-readmission]($./04.4-Model-Serving-patient-readmission) to enable realtime capabilities and instantly get insight for a specific patient.
- Explain model for our entire population or a specific patient to understand the risk factors and further personalize care with [04.5-Explainability-patient-readmission]($./04.5-Explainability-patient-readmission)